In [1]:
library(Seurat)
library(tidyverse)
library(DESeq2)
library(ComplexHeatmap)

The legacy packages maptools, rgdal, and rgeos, underpinning the sp package,
which was just loaded, were retired in October 2023.
Please refer to R-spatial evolution reports for details, especially
https://r-spatial.org/r/2023/05/15/evolution4.html.
It may be desirable to make the sf package available;
package maintainers should consider adding sf to Suggests:.

Attaching SeuratObject

── Attaching core tidyverse packages ──────────────────────────────────────────────────────────────── tidyverse 2.0.0 ──
✔ dplyr     1.1.3     ✔ readr     2.1.4
✔ forcats   1.0.0     ✔ stringr   1.5.0
✔ ggplot2   3.4.4     ✔ tibble    3.2.1
✔ lubridate 1.9.2     ✔ tidyr     1.3.0
✔ purrr     1.0.2     
── Conflicts ────────────────────────────────────────────────────────────────────────────────── tidyverse_conflicts() ──
✖ dplyr::filter() masks stats::filter()
✖ dplyr::lag()    masks stats::lag()
ℹ Use the conflicted package (<http://conflicted.r-lib.org/>) to force all conflicts to become errors
Loading

# Read in Raj resistant data

In [5]:
raj_resistant_cancer_type <- "melanoma"

raj_resistant <- readRDS(paste0("/data/CDSL_hannenhalli/Cole/projects/drug_treatment/data/processed_data/diverse_clonal_fates_data/raj_resistant_", raj_resistant_cancer_type, "_processed.rds"))

In [ ]:
sum(raj_resistant$seurat_clusters == 1)

# "Bulkify" Raj resistant data

In [54]:
# rowSums(raj_resistant[["RNA"]]@data[,colnames(raj_resistant)[raj_resistant$seurat_clusters == 1]])

# str(raj_resistant)

Formal class 'Seurat' [package "SeuratObject"] with 13 slots
  ..@ assays      :List of 3
  .. ..$ RNA       :Formal class 'Assay' [package "SeuratObject"] with 8 slots
  .. .. .. ..@ counts       :Formal class 'dgCMatrix' [package "Matrix"] with 6 slots
  .. .. .. .. .. ..@ i       : int [1:43946604] 7 21 22 31 34 38 44 47 54 80 ...
  .. .. .. .. .. ..@ p       : int [1:15962] 0 2944 6677 9358 12714 18937 23294 23719 24120 27206 ...
  .. .. .. .. .. ..@ Dim     : int [1:2] 21638 15961
  .. .. .. .. .. ..@ Dimnames:List of 2
  .. .. .. .. .. .. ..$ : chr [1:21638] "RP11-34P13.7" "AL627309.1" "AP006222.2" "RP4-669L17.10" ...
  .. .. .. .. .. .. ..$ : chr [1:15961] "S1_AAACCCAAGAACGCGT-1" "S1_AAACCCAAGAGCCATG-1" "S1_AAACCCAAGATTGACA-1" "S1_AAACCCAAGCCAGACA-1" ...
  .. .. .. .. .. ..@ x       : num [1:43946604] 1 1 42 1 1 1 3 4 2 1 ...
  .. .. .. .. .. ..@ factors : list()
  .. .. .. ..@ data         :Formal class 'dgCMatrix' [package "Matrix"] with 6 slots
  .. .. .. .. .. ..@ i       : 

In [6]:
raj_resistant_bulk <- matrix(NA, nrow=nrow(raj_resistant[["RNA"]]@data), ncol=nlevels(raj_resistant))

for(i in levels(raj_resistant)){
    
    raj_resistant_bulk[,as.numeric(i)] <- rowSums(raj_resistant[["RNA"]]@data[,colnames(raj_resistant)[raj_resistant$seurat_clusters == i]])
    
    
}

rownames(raj_resistant_bulk) <- rownames(raj_resistant[["RNA"]]@data)
colnames(raj_resistant_bulk) <- paste0("raj_resistant", 1:ncol(raj_resistant_bulk))

In [7]:
raj_resistant_bulk

raj_resistant1 raj_resistant2 raj_resistant3 raj_resistant4
HECW1         0               8              6             0          
LASP1      1156            3622           1735           676          
TMEM176A      0               4              3             0          
CYP26B1     123              52             26            74          
TFPI        250            3148           1315           175          
MTMR7         3               0              1             4          
ZMYND10      14              19              8            12          
ABCB5       760             117            130           999          
SLC25A13   1886            1163            654          1333          
SKAP2      3131            3744           2120          2575          
SLC25A5    9517           33092          14137          7739          
THSD7A        2               8              4             5          
PRKAR2B    2661             756            501           947          
KMT2E      8225            8134           5001          7719          
ITGA3       876           11571           4596           437          
TMEM98     2834            2176           1243          2219          
TNFRSF12A  4188           28748          10350          1160          
DLX6        344             191             84           136          
CCL26         3             942            273             6          
DBF4        344            4901           1116           241          
IFRD1      1867            5980           2260          1397          
SCIN          9               4              2            11          
PROM1         3               2              3             3          
GAS7       3420             943            930          1646          
CD79B         0               1              2             2          
PAX6          6               2              0             0          
BAIAP3        2               2              2             4          
MYLIP      1175             541            464           781          
CYTH3       840            1312            895           698          
AASS        623             281            109           384          
⋮          ⋮              ⋮              ⋮              ⋮             
7SK.2         47            128             99             36         
HIST1H2BG      1             20             12              4         
SOCS7         31             37             19             33         
TPTE         100             89             48             72         
AC009120.6    37             34             26             26         
CCL18         12             88            385              5         
ARHGAP23      12             57             26             11         
HIST1H4I      26             49             23             11         
ANKRD20A3     12              7              1              6         
MIR145        14            105             88             16         
HIST1H4E      39            142             58             47         
HIST1H2BF      7             63             14             12         
MARCKS     26359          21848          14728          15495         
CCL3          12           3541            462             17         
AC139100.2    24             89             42             33         
AL354822.1     2              5              8              0         
HIST1H2AB      0             13              2              1         
AC006994.2     7              8              6             10         
FAM230C        5              6              6              5         
AC083843.3     3              4              0              1         
AP000974.1    13             23              6             10         
PAGR1          6             12              8              4         
AL627171.2    10              8              7              7         
MIR3150A       3              9              5              1         
MIR146A      781            467    

# Read in Raj control data (memorySeq data)

In [8]:
if(raj_resistant_cancer_type == "breast"){
    raj_control_cancer_type <- "MDA"
} else if(raj_resistant_cancer_type == "melanoma"){
    raj_control_cancer_type <- "WM989"
}

raj_control <- readRDS(paste0("/data/CDSL_hannenhalli/Cole/projects/drug_treatment/data/processed_data/memorySeq_data/", raj_control_cancer_type,"_control_counts.rds"))

In [9]:
str(raj_control)

'data.frame':	20539 obs. of  47 variables:
 $ WM989-14: int  3 0 360 0 0 0 0 229 265 0 ...
 $ WM989-39: int  2 0 347 0 1 0 0 175 208 0 ...
 $ WM989-2 : int  5 1 576 1 0 0 0 333 344 0 ...
 $ WM989-1 : int  4 0 386 0 0 0 0 218 224 0 ...
 $ WM989-26: int  1 2 291 1 0 0 0 184 178 0 ...
 $ WM989-20: int  0 0 317 0 1 0 0 203 200 0 ...
 $ WM989-7 : int  5 0 251 0 1 0 1 199 186 0 ...
 $ WM989-30: int  6 1 361 0 1 0 0 200 184 0 ...
 $ WM989-37: int  1 0 277 0 0 0 1 190 177 0 ...
 $ WM989-47: int  3 0 309 0 1 0 1 191 168 0 ...
 $ WM989-17: int  1 1 172 1 1 0 0 136 146 0 ...
 $ WM989-10: int  0 1 251 0 0 2 0 169 173 0 ...
 $ WM989-38: int  2 1 405 2 1 0 0 217 208 0 ...
 $ WM989-9 : int  1 0 428 0 0 0 0 232 261 3 ...
 $ WM989-32: int  3 0 218 1 0 0 0 153 165 0 ...
 $ WM989-4 : int  5 1 324 0 0 0 0 219 204 0 ...
 $ WM989-29: int  3 0 372 0 2 0 0 206 185 0 ...
 $ WM989-23: int  8 0 278 0 0 0 1 202 205 0 ...
 $ WM989-33: int  1 0 350 1 0 0 0 179 195 0 ...
 $ WM989-5 : int  1 0 346 0 1 0 1 232 224 0 .

In [10]:
colnames(raj_control) <- paste0("raj_control", 1:ncol(raj_control))
dim(raj_control)

[1] 20539    47

In [11]:
shared_genes <- intersect(rownames(raj_resistant_bulk),rownames(raj_control))

raj_resistant_bulk <- raj_resistant_bulk[shared_genes,]
raj_control <- raj_control[shared_genes,]

# Merge Resistant and Control data

In [12]:
all_raj_data <- cbind(raj_resistant_bulk,raj_control)

In [14]:
# all_raj_data

In [15]:
coldata <- matrix(c(rep("resistant",ncol(raj_resistant_bulk)), rep("control", ncol(raj_control))), ncol=1)
colnames(coldata) <- c("condition")
rownames(coldata) <- colnames(all_raj_data)
coldata <- data.frame(coldata)

coldata$condition <- factor(coldata$condition)

# coldata

# Create DESeq DataSet Object

In [16]:
dds <- DESeqDataSetFromMatrix(countData = all_raj_data,
                      colData = coldata,
                      design = ~ condition)

dds

converting counts to integer mode



class: DESeqDataSet 
dim: 2726 60 
metadata(1): version
assays(1): counts
rownames(2726): HECW1 LASP1 ... AL627171.2 BTBD8
rowData names(0):
colnames(60): raj_resistant1 raj_resistant2 ... raj_control46
  raj_control47
colData names(1): condition

# Pre-filtering: remove rows with low gene counts

In [17]:
keep <- rowSums(counts(dds)) >= 10

dds <- dds[keep,]

In [18]:
dds$condition <- relevel(dds$condition, ref="control")

In [19]:
dds <- DESeq(dds)

estimating size factors

estimating dispersions

gene-wise dispersion estimates

mean-dispersion relationship

final dispersion estimates

fitting model and testing

-- replacing outliers and refitting for 134 genes
-- DESeq argument 'minReplicatesForReplace' = 7 
-- original counts are preserved in counts(dds)

estimating dispersions

fitting model and testing



In [24]:
res <- results(dds)
res

log2 fold change (MLE): condition resistant vs control 
Wald test p-value: condition resistant vs control 
DataFrame with 2726 rows and 6 columns
             baseMean log2FoldChange     lfcSE      stat      pvalue
            <numeric>      <numeric> <numeric> <numeric>   <numeric>
HECW1        0.493169       1.901125  0.906387   2.09748 3.59513e-02
LASP1      535.401156      -0.194746  0.100058  -1.94633 5.16146e-02
TMEM176A     0.441607       1.486682  0.738497   2.01312 4.41020e-02
CYP26B1     19.621698      -0.307734  0.233676  -1.31693 1.87864e-01
TFPI        88.787990       3.491378  0.195492  17.85947 2.43965e-71
...               ...            ...       ...       ...         ...
HIST1H2AB    0.212628       1.723553  0.988581   1.74346 8.12529e-02
AP000974.1   3.307708       0.425292  0.306720   1.38658 1.65570e-01
PAGR1       17.436979      -3.843336  0.251559 -15.27806 1.07086e-52
AL627171.2   2.268527       0.857915  0.416481   2.05991 3.94067e-02
BTBD8        4.359130     

In [21]:
res <- as.matrix(res)
saveRDS(res, paste0("/data/CDSL_hannenhalli/Cole/projects/drug_treatment/data/de_results/raj_", raj_resistant_cancer_type,"_vs_control_deseq_result.rds"))

# Create DE genesets for each resistant cluster in raj data by comparing each one to control samples

In [26]:
raj_cluster_de_genesets <- list()

for(i in colnames(raj_resistant_bulk)){
    
    cat(i,"\n")
    cols_to_use <- c(i,colnames(raj_control))
    
    curr_coldata <- coldata %>% 
                    filter(rownames(coldata) %in% cols_to_use)
    
    curr_counts <- all_raj_data[,colnames(all_raj_data) %in% cols_to_use]
    
    dds <- DESeqDataSetFromMatrix(countData = curr_counts,
                      colData = curr_coldata,
                      design = ~ condition)
    
    keep <- rowSums(counts(dds)) >= 10

    dds <- dds[keep,]
    
    dds$condition <- relevel(dds$condition, ref="control")
    
    dds <- DESeq(dds)
    
    res <- results(dds)
    
    all_de_genes <- cbind(res@rownames,data.frame(res@listData)) %>% 
    filter(log2FoldChange > 0 & padj < 0.05) %>% 
    arrange(padj) %>% 
    pull("res@rownames")
    
    all_de_genes <- all_de_genes[!grepl("^MT", all_de_genes)]
    all_de_genes <- all_de_genes[!grepl("^RPS", all_de_genes)]
    all_de_genes <- all_de_genes[!grepl("^RPL", all_de_genes)]
    
    raj_cluster_de_genesets <- append(raj_cluster_de_genesets, list(all_de_genes[1:500]))
}
                                      
names(raj_cluster_de_genesets) <- paste0(colnames(raj_resistant_bulk), "_de_genes")

raj_resistant1 


converting counts to integer mode

estimating size factors

estimating dispersions

gene-wise dispersion estimates

mean-dispersion relationship

final dispersion estimates

fitting model and testing

-- replacing outliers and refitting for 1417 genes
-- DESeq argument 'minReplicatesForReplace' = 7 
-- original counts are preserved in counts(dds)

estimating dispersions

fitting model and testing



raj_resistant2 


converting counts to integer mode

estimating size factors

estimating dispersions

gene-wise dispersion estimates

mean-dispersion relationship

final dispersion estimates

fitting model and testing

-- replacing outliers and refitting for 1666 genes
-- DESeq argument 'minReplicatesForReplace' = 7 
-- original counts are preserved in counts(dds)

estimating dispersions

fitting model and testing



raj_resistant3 


...

converting counts to integer mode

estimating size factors

estimating dispersions

gene-wise dispersion estimates

mean-dispersion relationship

final dispersion estimates

fitting model and testing

-- replacing outliers and refitting for 1468 genes
-- DESeq argument 'minReplicatesForReplace' = 7 
-- original counts are preserved in counts(dds)

estimating dispersions

fitting model and testing



raj_resistant12 


converting counts to integer mode

estimating size factors

estimating dispersions

gene-wise dispersion estimates

mean-dispersion relationship

final dispersion estimates

fitting model and testing

-- replacing outliers and refitting for 1539 genes
-- DESeq argument 'minReplicatesForReplace' = 7 
-- original counts are preserved in counts(dds)

estimating dispersions

fitting model and testing



raj_resistant13 


converting counts to integer mode

estimating size factors

estimating dispersions

gene-wise dispersion estimates

mean-dispersion relationship

final dispersion estimates

fitting model and testing

-- replacing outliers and refitting for 1483 genes
-- DESeq argument 'minReplicatesForReplace' = 7 
-- original counts are preserved in counts(dds)

estimating dispersions

fitting model and testing



In [32]:
saveRDS(raj_cluster_de_genesets, paste0("/data/CDSL_hannenhalli/Cole/projects/drug_treatment/data/genesets/raj_",raj_resistant_cancer_type,"_clusters_vs_control_de_genesets_500.rds"))

In [28]:
raj_cluster_de_genesets

$raj_resistant1_de_genes
  [1] "VMP1"       "DLX5"       "PHACTR1"    "ID2"        "CTGF"      
  [6] "FAM210B"    "SOX4"       "CITED1"     "BTG1"       "TFAP2A"    
 [11] "SORBS2"     "EEF1A1"     "EIF4A1"     "CITED2"     "DLC1"      
 [16] "TUBA1A"     "POLR2J3"    "ID4"        "ZFP36L1"    "TXNIP"     
 [21] "TSC22D1"    "CRYAB"      "FAM129A"    "MEF2C"      "PALLD"     
 [26] "SPTSSA"     "CAPN3"      "BRI3"       "NR2F2"      "LIMA1"     
 [31] "PNRC1"      "HMGB1"      "ANXA2"      "MRPS6"      "FAM89A"    
 [36] "JUN"        "CAV1"       "CRYL1"      "H3F3B"      "PDZRN3"    
 [41] "NLRP1"      "ARL4C"      "NUPR1"      "DDIT3"      "PDLIM3"    
 [46] "STXBP6"     "ARID5B"     "SNAI2"      "KLF6"       "S100A10"   
 [51] "RHOBTB3"    "PTEN"       "IMMP2L"     "ARHGAP24"   "TMEM59"    
 [56] "GPR137B"    "HIST1H2AC"  "TGFBR2"     "YPEL3"      "CCND1"     
 [61] "GADD45B"    "RAP1B"      "PSD3"       "CD68"       "TUBB2A"    
 [66] "TGIF1"      "AP1S2"      "HSPA1A"     "FABP5"      "NUDT4"     
 [71] "TCF7L1"     "ARL4A"      "RDH10"      "S100A1"     "MARCKS"    
 [76] "SATB1"      "HEBP1"      "ARSG"       "CAMK2N1"    "RGS16"     
 [81] "XYLT1"      "PAX3"       "RIN2"       "EEF1B2"     "PMEPA1"    
 [86] "TERF1"      "EPS8"       "ARMCX3"     "TPT1"       "MYLIP"     
 [91] "MAP2"       "WSB1"       "PTMA"       "TPM1"       "PRKAR2B"   
 [96] "TUBA1B"     "HERPUD1"    "FTL"        "ANKRD10"    "HABP4"     
[101] "PINK1"      "ASAP2"      "VIM"        "ZNF362"     "POPDC3"    
[106] "LAPTM4A"    "EGLN3"      "SWAP70"     "AGAP1"      "LMO7"      
[111] "SPARC"      "PMP22"      "SNAPC1"     "TMSB4X"     "SAMD4A"    
[116] "HES1"       "CBLB"       "FOS"        "SPATA6"     "B2M"       
[121] "DYNC1I1"    "HLA-A"      "CD59"       "ST6GALNAC2" "DACT1"     
[126] "IFIT1"      "CSRP2"      "CCPG1"      "NDUFA4"     "MMP2"      
[131] "FOXD1"      "CD44"       "NBPF10"     "ARSJ"       "FAM177A1"  
[136] "CYSTM1"     "SKAP2"      "WDR60"      "NPM1"       "PCMTD1"    
[141] "NHLRC3"     "IER2"       "FANCL"      "FBXO32"     "CALM2"     
[146] "S100A11"    "SAMD5"      "CEBPD"      "C1orf56"    "CALD1"     
[151] "MAP4"       "LITAF"      "SLITRK6"    "RAB13"      "RAB32"     
[156] "HIST2H2BE"  "GNAI1"      "STON1"      "NR2F1"      "RGS2"      
[161] "EPB41L3"    "GPM6B"      "SH3BP5"     "RIMS2"      "PRELP"     
[166] "DKK1"       "TMSB10"     "COL1A1"     "IFI6"       "CBX7"      
[171] "ID3"        "MFGE8"      "ADAM23"     "NEDD9"      "HBP1"      
[176] "CDKN2D"     "NAIP"       "DIP2C"      "ITM2B"      "IGFBP7"    
[181] "POLM"       "RASSF4"     "CPQ"        "MYL6"       "EEF1D"     
[186] "KLHL24"     "CDH19"      "F2R"        "MPC2"       "DDAH1"     
[191] "JUND"       "ACTA2"      "HIST1H1C"   "CCDC71L"    "KHDRBS3"   
[196] "KANK2"      "CXXC5"      "PGRMC2"     "LURAP1L"    "SIPA1L2"   
[201] "ITGA2"      "RHOB"       "GNG11"      "PKD2"       "EGR1"      
[206] "AEBP1"      "EDNRB"      "PPP1R14B"   "UGT2B7"     "TAGLN2"    
[211] "SERPINE2"   "SOCS3"      "LMO4"       "GTF2IRD2B"  "H2AFJ"     
[216] "ENOX1"      "IL17D"      "RAPH1"      "SH3BGRL3"   "ID1"       
[221] "NRBP2"      "SAMD11"     "XBP1"       "TGFB1I1"    "RTN4"      
[226] "IFITM3"     "TMEM98"     "TPM4"       "COL5A2"     "JAG1"      
[231] "SMURF2"     "ZEB2"       "NTRK2"      "C1orf198"   "LRCH3"     
[236] "MLPH"       "NFIB"       "GPNMB"      "PKIG"       "HIST1H1D"  
[241] "MXI1"       "EVA1A"      "PDGFA"      "RUNX1"      "FAM167B"   
[246] "HIST1H2BK"  "DLX6"       "BCAN"       "ST8SIA1"    "PCDH1"     
[251] "SHC4"       "CYCS"       "ADAMTS9"    "C6orf48"    "PPIB"      
[256] "ALCAM"      "ARGLU1"     "PLXNB1"     "ABLIM3"     "DSTN"      
[261] "ITGA1"      "NAP1L1"     "N4BP2L2"    "PPIA"       "CIR1"      
[266] "FKBP1B"     "OTUD1"      "RNF169"     "POLR2F"     "ATP5E"     
[271] "ACTG1"      "FTH1"       "ARPC1B"     "KDELR3"     "PLXDC2"    
[276] "LIMCH1"     "GULP1"      "MAFB"       "GK"         "FSTL3"     

In [29]:
temp <- readRDS("/data/CDSL_hannenhalli/Cole/projects/drug_treatment/data/processed_data/sciPlex_data/A549_processed_filtered.rds")

In [31]:
temp$treatment_stage

A01_E09_RT_BC_100_Lig_BC_245 A01_E09_RT_BC_100_Lig_BC_306 
                      "post"                       "post" 
A01_E09_RT_BC_101_Lig_BC_109 A01_E09_RT_BC_101_Lig_BC_229 
                       "pre"                       "post" 
A01_E09_RT_BC_101_Lig_BC_280  A01_E09_RT_BC_101_Lig_BC_86 
                      "post"                       "post" 
A01_E09_RT_BC_102_Lig_BC_215 A01_E09_RT_BC_102_Lig_BC_262 
                      "post"                       "post" 
A01_E09_RT_BC_102_Lig_BC_265 A01_E09_RT_BC_102_Lig_BC_332 
                      "post"                       "post" 
 A01_E09_RT_BC_102_Lig_BC_35 A01_E09_RT_BC_102_Lig_BC_379 
                      "post"                       "post" 
A01_E09_RT_BC_103_Lig_BC_162 A01_E09_RT_BC_103_Lig_BC_167 
                      "post"                       "post" 
A01_E09_RT_BC_103_Lig_BC_236 A01_E09_RT_BC_103_Lig_BC_311 
                      "post"                       "post" 
A01_E09_RT_BC_104_Lig_BC_375 A01_E09_RT_BC_104_Lig_BC_382 
                      "post"                       "post" 
 A01_E09_RT_BC_104_Lig_BC_96 A01_E09_RT_BC_105_Lig_BC_132 
                      "post"                       "post" 
A01_E09_RT_BC_105_Lig_BC_257 A01_E09_RT_BC_106_Lig_BC_154 
                      "post"                       "post" 
A01_E09_RT_BC_108_Lig_BC_256 A01_E09_RT_BC_109_Lig_BC_189 
                      "post"                       "post" 
A01_E09_RT_BC_109_Lig_BC_213  A01_E09_RT_BC_109_Lig_BC_62 
                      "post"                       "post" 
 A01_E09_RT_BC_10_Lig_BC_239  A01_E09_RT_BC_10_Lig_BC_324 
                      "post"                       "post" 
A01_E09_RT_BC_112_Lig_BC_159 A01_E09_RT_BC_112_Lig_BC_206 
                      "post"                       "post" 
A01_E09_RT_BC_112_Lig_BC_251 A01_E09_RT_BC_114_Lig_BC_341 
                      "post"                       "post" 
 A01_E09_RT_BC_114_Lig_BC_47 A01_E09_RT_BC_115_Lig_BC_129 
                      "post"                       "post" 
 A01_E09_RT_BC_115_Lig_BC_52  A01_E09_RT_BC_115_Lig_BC_54 
                      "post"                       "post" 
 A01_E09_RT_BC_115_Lig_BC_90 A01_E09_RT_BC_116_Lig_BC_180 
                      "post"                       "post" 
A01_E09_RT_BC_116_Lig_BC_193 A01_E09_RT_BC_116_Lig_BC_215 
                      "post"                       "post" 
A01_E09_RT_BC_118_Lig_BC_143 A01_E09_RT_BC_119_Lig_BC_146 
                      "post"                       "post" 
A01_E09_RT_BC_119_Lig_BC_283  A01_E09_RT_BC_119_Lig_BC_51 
                      "post"                       "post" 
 A01_E09_RT_BC_119_Lig_BC_60 A01_E09_RT_BC_120_Lig_BC_131 
                      "post"                       "post" 
A01_E09_RT_BC_120_Lig_BC_323 A01_E09_RT_BC_121_Lig_BC_111 
                      "post"                       "post" 
 A01_E09_RT_BC_121_Lig_BC_27 A01_E09_RT_BC_121_Lig_BC_376 
                      "post"                       "post" 
A01_E09_RT_BC_122_Lig_BC_102 A01_E09_RT_BC_122_Lig_BC_104 
                      "post"                       "post" 
A01_E09_RT_BC_122_Lig_BC_233 A01_E09_RT_BC_122_Lig_BC_373 
                      "post"                       "post" 
 A01_E09_RT_BC_122_Lig_BC_87 A01_E09_RT_BC_123_Lig_BC_144 
                      "post"                       "post" 
A01_E09_RT_BC_124_Lig_BC_378 A01_E09_RT_BC_125_Lig_BC_370 
                      "post"                        "pre" 
A01_E09_RT_BC_126_Lig_BC_323 A01_E09_RT_BC_128_Lig_BC_107 
                      "post"                       "post" 
A01_E09_RT_BC_128_Lig_BC_154 A01_E09_RT_BC_128_Lig_BC_265 
                      "post"                       "post" 
 A01_E09_RT_BC_128_Lig_BC_59  A01_E09_RT_BC_128_Lig_BC_75 
                      "post"                       "post" 
 A01_E09_RT_BC_129_Lig_BC_15 A01_E09_RT_BC_129_Lig_BC_162 
                      "post"                       "post" 
A01_E09_RT_BC_129_Lig_BC_210 A01_E09_RT_BC_130_Lig_BC_132 
                      "post"                   